# Using Gymnasium to do simple trading algorithm

In [ ]:
!pip install gymnasium 
!pip install yfinance
!pip install "stable-baselines3[extra]>=2.0.0a4"
!pip install ipywidgets
!pip install pandas
!pip install matplotlib
!pip install torch
!pip install tqdm

In [3]:
import gymnasium as gym
import torch
import numpy as np
import yfinance as yf
import datetime
import pandas as pd
from tqdm import tqdm
from matplotlib import pyplot as plt
from stable_baselines3.common.callbacks import BaseCallback
from stable_baselines3.common.logger import configure

In [4]:
class TensorboardCallback(BaseCallback):
    def __init__(self, verbose=0):
        super(TensorboardCallback, self).__init__(verbose)
        self.episode_rewards = []

    def _on_step(self) -> bool:
        # Log custom metrics across all environments
        for i in range(len(self.locals["infos"])):
            if "current_networth" in self.locals["infos"][i]:
                self.logger.record(f"networth/env_{i}", self.locals["infos"][i]["current_networth"])
            if "current_gain" in self.locals["infos"][i]:
                self.logger.record(f"gain/env_{i}", self.locals["infos"][i]["diff_norm"])
            
            #log reward for all envs in each step
            if "episode" in self.locals["infos"][i]:
                episode_reward = self.locals["infos"][i]["episode"]["r"]
                self.episode_rewards.append(episode_reward)
                self.logger.record(f"reward/env_{i}", episode_reward)
        #log average reward for all envs in each step
        if len(self.episode_rewards) > 0:
            avg_reward = np.mean(self.episode_rewards)
            self.logger.record("reward/average", avg_reward)
            
        # log average gain
        if "current_gain" in self.locals["infos"][0]:
            avg_gain = np.mean([info["diff_norm"] for info in self.locals["infos"]])
            self.logger.record("gain/average", avg_gain)
            
        return True

        # Log PPO losses
    def _on_training_step(self) -> bool:
        loss_info = self.locals["loss"] if "loss" in self.locals else {}
        self.logger.record("loss/policy_loss", loss_info.get("policy_loss", 0))
        self.logger.record("loss/value_loss", loss_info.get("value_loss", 0))
        self.logger.record("loss/entropy_loss", loss_info.get("entropy_loss", 0))

In [5]:

class TradingEnv(gym.Env):
    def __init__(self, stock='AAPL', minbuy=10, gran='1d', period='max', shares=3, boughtat="2023-12-01", randomize=True, seed=0, verbose=False):
        super(TradingEnv, self).__init__()
        self.running_mean = 0
        self.running_std = 1  
        self.decay_factor = 0.99  
        self.epsilon = 1e-7  
        
        self.stock = stock
        self.minbuy = minbuy
        self.gran = gran
        self.period = period
        self.shares = shares
        self.boughtat = boughtat
        self.seed = seed
        self.randomize = randomize
        self.max_networth = 0
        self.print = verbose
        self.streak = 0
        self.is_init = True
        
        if self.gran in ['5m', '15m', '30m']:
            print("[WARNING] Data granularity can only go back to 60 Days Maxiumum")
        if self.gran in ['1h', '60m']:
            print("[WARNING] Data granularity can only go back to 730 Days Maxiumum")
        self.random_symbols = [
            "NVDA" , "AMZN", "GOOGL", "MSFT", "AAPL", "META", "NVDA", "ADBE", "NFLX", "NANC", "KRUZ", "VOO", "FTEC", "TSLA"
        ]
        self.random_gran_period_pairs = {
            '1d' : ['max']
        }
        if self.randomize:
            self._randomize()
        else:
            self.data = yf.Ticker(self.stock).history(period=self.period, interval=self.gran, auto_adjust=True)
        
        self._init_obs()

        self.observation_space = gym.spaces.Box(
            low=-np.inf, high=np.inf, shape=(1, 48), dtype=np.float32
        )
        self.action_space = gym.spaces.Discrete(2)
        self.networth_rewd = 0
        
    def _init_obs(self):
        self.current_day = self.boughtat
        self.cur_indx = self.data.index.get_loc(self.current_day)
        self.init_networth = self.shares * self.data.loc[self.boughtat, 'Close']
        self.networth = self.init_networth
        self.previous_open_close = self.data.loc[self.boughtat, 'Open'], self.data.loc[self.boughtat, 'Close']
        self.previous_high_low = self.data.loc[self.boughtat, 'High'], self.data.loc[self.boughtat, 'Low']
        self.previous_volume = self.data.loc[self.boughtat, 'Volume']
        self.previous_momentum_wk = self._calculate_momentum(7)
        self.previous_momentum_mon = self._calculate_momentum(30)
        self.previous_wk_close = np.zeros((1,7))
        self.previous_mo_close = np.zeros((1,30))
        self.bought_price = self.data.loc[self.boughtat, 'Close']
        self.current_shares = self.shares
        self.relneworth = 0
        self.current_action = 0
        self.max_networth = 0
        self.streak = 0
        self.is_init = True

        self.has_position = True
        self.previous_obs = np.zeros((1, 48)).astype(np.float32)
        
        
    def _randomize(self):
        self.random_seed = np.random.randint(0, 100)
        np.random.seed(self.random_seed)
        # Randomly select number of shares from 1 to 10
        self.shares = np.random.randint(1, 10)
        
        # Randomly select granularity and period
        while True:
            self.gran = np.random.choice(list(self.random_gran_period_pairs.keys()))
            self.period = np.random.choice(self.random_gran_period_pairs[self.gran])
            
            # Randomly select a stock
            self.stock = np.random.choice(self.random_symbols)
            
            try:
                # Fetch data for the randomized stock, period, and granularity
                self.data = yf.Ticker(self.stock).history(period=self.period, interval=self.gran, auto_adjust=True)
                self.boughtat = np.random.choice(self.data.index[31:])
                break
            except:
                continue
    
    def reset(self, seed=0):
        super(TradingEnv, self).reset()
        if self.randomize:
            self._randomize()
        else:
            self.data = yf.Ticker(self.stock).history(period=self.period, interval=self.gran, auto_adjust=True)
        self.seed = seed
        self._init_obs()
        info = {
            "init_networth": self.init_networth,
            "current_networth": self.networth,
            "current_action": self.current_action,
            "current_gain": self.relneworth,
            "diff": self.networth - self.init_networth,
            "diff_norm" : (self.networth - self.init_networth) / self.init_networth,
            "reward": self._reward(self.current_action),
            
        }
        return self.previous_obs, info
    
    def _calculate_momentum(self, interval):
        if self.cur_indx - interval < 0:
            return 0  # Avoid accessing invalid index
        past_price = self.data.iloc[self.cur_indx - interval]['Close']
        current_price = self.data.iloc[self.cur_indx]['Close']
        return (current_price - past_price) / past_price

    
    def _get_previous_close(self, interval):
        return self.data.loc[self.data.index[self.cur_indx-interval:self.cur_indx], 'Close'].to_numpy().reshape(1, interval)
    
    def step(self, action):
        if action == 1:
            if self.has_position:
                self.relneworth = self.current_shares * (self.previous_open_close[1] - self.bought_price)
                self.has_position = False
                self.networth += self.relneworth
            else:
                self.has_position = True
                self.relneworth = 0
            self.streak = 0
            self.bought_price = self.previous_open_close[1]
            self.current_action = 1
            self.max_networth = 0
        else:
            self.streak += 1
            self.current_action = 0
            self.relneworth = self.shares * (self.previous_open_close[1] - self.bought_price)
            if self.relneworth > self.max_networth:
                self.max_networth = self.relneworth
            
        self.cur_indx += 1
        info = {
            "init_networth": self.init_networth,
            "current_networth": self.networth,
            "current_action": self.current_action,
            "current_gain": self.relneworth,
            "diff": self.networth - self.init_networth,
            "diff_norm" : (self.networth - self.init_networth) / self.init_networth,
            "reward": self._reward(self.current_action),
        }
        try:
            self.current_day = self.data.index[self.cur_indx]
            terminated = False
            truncated = False
        except IndexError:
            print("[INFO] Data Exhausted")
            self.current_day = self.data.index[-1]
            terminated = False
            truncated = True
            return (
                self.prev_obs,
                self._reward(action),
                True,
                True,
                info
            )

        self.previous_open_close = np.array([self.data.loc[self.current_day, 'Open'], self.data.loc[self.current_day, 'Close']])
        self.previous_high_low = np.array([self.data.loc[self.current_day, 'High'], self.data.loc[self.current_day, 'Low']])
        self.previous_volume = np.array([self.data.loc[self.current_day, 'Volume']])
        self.previous_momentum_wk = self._calculate_momentum(7)
        self.previous_momentum_mon = self._calculate_momentum(30)
        self.previous_wk_close = self.data.loc[self.data.index[self.cur_indx-7:self.cur_indx], 'Close'].to_numpy()
        self.previous_mo_close = self.data.loc[self.data.index[self.cur_indx-30:self.cur_indx], 'Close'].to_numpy()

        # Flatten and construct the observation array
        observation = np.concatenate([
            self.previous_open_close.flatten(), # 2
            self.previous_high_low.flatten(), # 2
            self.previous_volume.flatten(), # 1
            self.previous_wk_close.flatten(), # 7
            self.previous_mo_close.flatten(), # 30
            np.array([
                self.previous_momentum_wk, # 1
                self.previous_momentum_mon, # 1
                self.bought_price, # 1
                self.current_shares, # 1
                self.relneworth, # 1
                self.current_action # 1
            ])
        ]).astype(np.float32)
        
        observation = observation.reshape(1, -1)
        self.prev_obs = observation

        # Termination terms
        if self.networth < (self.init_networth * 0.90):
            # print("[INFO] Terminated due to Loss")
            terminated = True
        truncated = False
        if self.cur_indx >= len(self.data.index) - 1:
            truncated = True


        # Reward
        reward = self._reward(action)
        
        self.is_init = False

        # Additional Info
        if self.print:
            print(" ")
            print("---------------------------------------------------------")
            print(f"[INFO] Current Stock: {self.stock}")
            print(f"[INFO] Current Day: {self.current_day}")
            print(f"[INFO] Current Open: {self.previous_open_close[0]}")
            print(f"[INFO] Current Net Worth: {self.networth}")
            print(f"[INFO] Holding Share: {self.has_position}")
            print(f"[INFO] Current Share Net Worth: {self.relneworth}")
            print("[INFO] Current Action: " + ("Hold" if self.current_action == 0 else "Sell" if self.current_action == 1 and not self.has_position else "Buy"))
            print("---------------------------------------------------------")

        return (
            observation,
            reward,
            terminated,
            truncated,
            info
        )
    def _reward(self, action):
        reward_weights = {
            "relnetworth": 0.7,
            "streak": 0.3,
            
        }
        
        self.networth_rewd, self.streak_rewd = 0, 0
        
        # self.networth_rewd = self.relneworth
        if self.has_position:
            if self.relneworth < self.max_networth and self.max_networth > 0:
                self.networth_rewd = (self.relneworth - self.max_networth)/self.max_networth
            else:
                self.networth_rewd = self.relneworth / self.bought_price
        else:
            self.networth_rewd = (self.relneworth / self.bought_price) * -1
        
        if (self.streak < self.minbuy and not self.is_init) and action == 1:
            self.streak_rewd = -10
        else:
            self.streak_rewd = 2
        
        # Optionally clip the normalized reward to avoid very large values
        reward_min = -7
        reward_max = 7
        
        normalized_reward = reward_weights["relnetworth"] * self.networth_rewd + reward_weights["streak"] * self.streak_rewd
        normalized_reward = np.clip(normalized_reward, reward_min, reward_max)
        
        return normalized_reward
    
    def render(self):
        # Graph out the stock price with the buy and sell points
        pass
    
    def close(self):
        pass

## Training

In [6]:
from stable_baselines3 import PPO, A2C, DQN
from stable_baselines3.common.env_util import make_vec_env

In [7]:
env = TradingEnv(randomize=True, verbose=False)

In [8]:
def exponential_schedule(initial_value):
    def func(progress_remaining):
        return initial_value * np.exp(-10 * (1 - progress_remaining))
    return func

def adaptive_ent_coef(progress_remaining):
    return 0.02 * (1 - progress_remaining)

In [9]:
log_dir = "./tensorboard_logs/"
n_envs = 10
n_steps = 1000
batch_size = 500
ent_coef = 0.02
new_logger = configure(log_dir, ["stdout", "tensorboard"])
vec_env = make_vec_env(TradingEnv, n_envs=n_envs)
ent_coef = 0.02  # Default: 0.0 (increase to encourage exploration)
model = PPO("MlpPolicy", vec_env, verbose=1, device="cpu", n_steps=n_steps, tensorboard_log=log_dir, batch_size=batch_size, learning_rate=exponential_schedule(1e-4), ent_coef=ent_coef)
model.learn(total_timesteps=30000000, progress_bar=True, tb_log_name="stock_ppo", callback=TensorboardCallback(), log_interval=1)

Logging to ./tensorboard_logs/
Using cpu device
Logging to ./tensorboard_logs/stock_ppo_2


Output()

----------------------------------
| gain/              |           |
|    average         | 0.329     |
|    env_0           | 0.014     |
|    env_1           | 0.109     |
|    env_2           | 0.537     |
|    env_3           | 0.155     |
|    env_4           | 0.0866    |
|    env_5           | 0.357     |
|    env_6           | 1.46      |
|    env_7           | -0.0522   |
|    env_8           | 0.351     |
|    env_9           | 0.272     |
| networth/          |           |
|    env_0           | 2.25      |
|    env_1           | 37.3      |
|    env_2           | 2.16e+03  |
|    env_3           | 63.5      |
|    env_4           | 1.53e+03  |
|    env_5           | 245       |
|    env_6           | 528       |
|    env_7           | 171       |
|    env_8           | 1.9e+03   |
|    env_9           | 186       |
| reward/            |           |
|    average         | -322      |
|    env_0           | -1.23e+03 |
|    env_1           | -387      |
|    env_2          

-----------------------------------------
| gain/                   |             |
|    average              | 1.2         |
|    env_0                | 1.11        |
|    env_1                | 2.16        |
|    env_2                | 0.034       |
|    env_3                | 3.93        |
|    env_4                | 0.168       |
|    env_5                | 0.794       |
|    env_6                | 0.962       |
|    env_7                | 0.141       |
|    env_8                | 0.635       |
|    env_9                | 2.05        |
| networth/               |             |
|    env_0                | 116         |
|    env_1                | 106         |
|    env_2                | 186         |
|    env_3                | 11          |
|    env_4                | 1.64e+03    |
|    env_5                | 323         |
|    env_6                | 66          |
|    env_7                | 206         |
|    env_8                | 2.29e+03    |
|    env_9                | 445   

-----------------------------------------
| gain/                   |             |
|    average              | 3.66        |
|    env_0                | 0.739       |
|    env_1                | 13.9        |
|    env_2                | 0.116       |
|    env_3                | 11.3        |
|    env_4                | 1.14        |
|    env_5                | 0.149       |
|    env_6                | 7.15        |
|    env_7                | 0.659       |
|    env_8                | 1.26        |
|    env_9                | 0.195       |
| networth/               |             |
|    env_0                | 570         |
|    env_1                | 500         |
|    env_2                | 201         |
|    env_3                | 27.3        |
|    env_4                | 4.74        |
|    env_5                | 1.61e+03    |
|    env_6                | 274         |
|    env_7                | 299         |
|    env_8                | 124         |
|    env_9                | 2.65  

...

--------------------------------------
| gain/                   |          |
|    average              | 13.3     |
|    env_0                | 0.186    |
|    env_1                | 0.644    |
|    env_2                | 7.22     |
|    env_3                | 4.33     |
|    env_4                | 0        |
|    env_5                | 15.5     |
|    env_6                | 69.1     |
|    env_7                | 1.3      |
|    env_8                | 0.55     |
|    env_9                | 34.6     |
| networth/               |          |
|    env_0                | 2.63     |
|    env_1                | 24.3     |
|    env_2                | 18.3     |
|    env_3                | 78.8     |
|    env_4                | 312      |
|    env_5                | 556      |
|    env_6                | 156      |
|    env_7                | 124      |
|    env_8                | 52.1     |
|    env_9                | 390      |
| reward/                 |          |
|    average             

---------------------------------------
| gain/                   |           |
|    average              | 14.3      |
|    env_0                | 3.44      |
|    env_1                | 3.33      |
|    env_2                | 38.4      |
|    env_3                | 6.68      |
|    env_4                | 0.196     |
|    env_5                | 0.478     |
|    env_6                | 0.784     |
|    env_7                | 5.09      |
|    env_8                | 1.43      |
|    env_9                | 82.8      |
| networth/               |           |
|    env_0                | 9.86      |
|    env_1                | 64        |
|    env_2                | 87.5      |
|    env_3                | 113       |
|    env_4                | 64.5      |
|    env_5                | 317       |
|    env_6                | 431       |
|    env_7                | 328       |
|    env_8                | 81.6      |
|    env_9                | 917       |
| reward/                 |           |


---------------------------------------
| gain/                   |           |
|    average              | 5.33      |
|    env_0                | 34.6      |
|    env_1                | 0.421     |
|    env_2                | 0.0945    |
|    env_3                | 6.98      |
|    env_4                | -0.0176   |
|    env_5                | 4.01      |
|    env_6                | 0.728     |
|    env_7                | 0         |
|    env_8                | 6.29      |
|    env_9                | 0.181     |
| networth/               |           |
|    env_0                | 79        |
|    env_1                | 1.99e+03  |
|    env_2                | 1.54e+03  |
|    env_3                | 118       |
|    env_4                | 54        |
|    env_5                | 1.08e+03  |
|    env_6                | 3.84      |
|    env_7                | 2.22      |
|    env_8                | 245       |
|    env_9                | 213       |
| reward/                 |           |


--------------------------------------
| gain/                   |          |
|    average              | 6.56     |
|    env_0                | 0.375    |
|    env_1                | 0.0691   |
|    env_2                | 0.672    |
|    env_3                | 9.53     |
|    env_4                | 2.95     |
|    env_5                | 6.47     |
|    env_6                | 14.1     |
|    env_7                | 5.57     |
|    env_8                | 25.4     |
|    env_9                | 0.487    |
| networth/               |          |
|    env_0                | 46.2     |
|    env_1                | 2.37     |
|    env_2                | 2.35e+03 |
|    env_3                | 156      |
|    env_4                | 58.3     |
|    env_5                | 1.6e+03  |
|    env_6                | 33.4     |
|    env_7                | 14.6     |
|    env_8                | 888      |
|    env_9                | 268      |
| reward/                 |          |
|    average             

---------------------------------------
| gain/                   |           |
|    average              | 2.34      |
|    env_0                | 2.42      |
|    env_1                | 0.833     |
|    env_2                | 0.445     |
|    env_3                | 17.8      |
|    env_4                | 1.34      |
|    env_5                | -0.0308   |
|    env_6                | 0.182     |
|    env_7                | 0.171     |
|    env_8                | 0.0167    |
|    env_9                | 0.226     |
| networth/               |           |
|    env_0                | 115       |
|    env_1                | 20        |
|    env_2                | 2.03e+03  |
|    env_3                | 278       |
|    env_4                | 34.6      |
|    env_5                | 303       |
|    env_6                | 2.63      |
|    env_7                | 171       |
|    env_8                | 34.2      |
|    env_9                | 221       |
| reward/                 |           |


In [10]:
#save model
model.save("stock_ppo_model_30m")

## Evaluation of the model

In [19]:
eval_model = PPO.load("stock_ppo_model_30m", env=vec_env)

In [22]:

env = make_vec_env(TradingEnv, n_envs=1, env_kwargs={"randomize": False, "verbose": True, "stock": "AAPL", "shares": 3, "boughtat": "2023-11-13"})
obs = env.reset()
netgains = 0
for j in range(300):
    action, _states = eval_model.predict(obs)
    obs, rewards, done, info = env.step(action)
    print(f"Reward {rewards}")
    if done or j == 299:
        print(f"Final gain: {info[0]['diff']}")
        break

 
---------------------------------------------------------
[INFO] Current Stock: AAPL
[INFO] Current Day: 2023-11-14 00:00:00-05:00
[INFO] Current Open: 186.579792942837
[INFO] Current Net Worth: 551.0912933349609
[INFO] Holding Share: True
[INFO] Current Share Net Worth: 0.0
[INFO] Current Action: Hold
---------------------------------------------------------
Reward [0.6]
 
---------------------------------------------------------
[INFO] Current Stock: AAPL
[INFO] Current Day: 2023-11-15 00:00:00-05:00
[INFO] Current Open: 186.72892111610665
[INFO] Current Net Worth: 551.0912933349609
[INFO] Holding Share: True
[INFO] Current Share Net Worth: 7.8727569580078125
[INFO] Current Action: Hold
---------------------------------------------------------
Reward [0.6300001]
 
---------------------------------------------------------
[INFO] Current Stock: AAPL
[INFO] Current Day: 2023-11-16 00:00:00-05:00
[INFO] Current Open: 188.43864070160558
[INFO] Current Net Worth: 551.0912933349609
[INFO]